In [1]:
%pip install seaborn

Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy
import pandas as pd
import os
import requests
import json
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import StandardScaler,MinMaxScaler, OneHotEncoder,StandardScaler
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.manifold import TSNE
from sklearn.compose import ColumnTransformer
%matplotlib inline
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

import seaborn as sns
pd.options.display.max_rows = 999

In [3]:
url = "https://api.repliers.io/listings?propertyType=detached&class=residential"

headers = {
    "accept": "application/json",
    "content-type": "application/json",
    "REPLIERS-API-KEY": ""
}

post = requests.post(url, headers=headers)
response_dict = json.loads(post.text)
df = pd.json_normalize(response_dict['listings'])
pd.set_option('display.max_columns', None)

In [4]:
df.columns.to_list()

['mlsNumber',
 'resource',
 'status',
 'class',
 'type',
 'listPrice',
 'listDate',
 'lastStatus',
 'soldPrice',
 'soldDate',
 'originalPrice',
 'assignment',
 'images',
 'photoCount',
 'daysOnMarket',
 'occupancy',
 'updatedOn',
 'coopCompensation',
 'openHouse',
 'rooms',
 'agents',
 'boardId',
 'address.area',
 'address.city',
 'address.country',
 'address.district',
 'address.majorIntersection',
 'address.neighborhood',
 'address.streetDirection',
 'address.streetName',
 'address.streetNumber',
 'address.streetSuffix',
 'address.unitNumber',
 'address.zip',
 'address.state',
 'address.communityCode',
 'address.streetDirectionPrefix',
 'map.latitude',
 'map.longitude',
 'map.point',
 'permissions.displayAddressOnInternet',
 'permissions.displayPublic',
 'permissions.displayInternetEntireListing',
 'details.airConditioning',
 'details.basement1',
 'details.basement2',
 'details.centralVac',
 'details.den',
 'details.description',
 'details.elevator',
 'details.exteriorConstruction1',

In [5]:
df.isna().mean().reset_index().sort_values(by=0)

index     0
0                                    mlsNumber  0.00
37                                map.latitude  0.00
38                               map.longitude  0.00
39                                   map.point  0.00
40        permissions.displayAddressOnInternet  0.00
41                   permissions.displayPublic  0.00
42    permissions.displayInternetEntireListing  0.00
43                     details.airConditioning  0.00
44                           details.basement1  0.00
48                         details.description  0.00
50               details.exteriorConstruction1  0.00
54                              details.garage  0.00
55                             details.heating  0.00
56                        details.numBathrooms  0.00
58                         details.numBedrooms  0.00
63                            details.numRooms  0.00
66                        details.propertyType  0.00
68                               details.style  0.00
69                        details.swimmingPool  0.00
97                               details.sewer  0.00
98                          details.familyRoom  0.00
110                        details.numKitchens  0.00
117                        details.waterSource  0.00
120                          details.bathrooms  0.00
135                           nearby.amenities  0.00
136                       office.brokerageName  0.00
140                  timestamps.listingUpdated  0.00
141                   timestamps.photosUpdated  0.00
145                timestamps.listingEntryDate  0.00
148                      timestamps.expiryDate  0.00
34                               address.state  0.00
33                                 address.zip  0.00
151               timestamps.repliersUpdatedOn  0.00
2                                       status  0.00
17                            coopCompensation  0.00
20                                      agents  0.00
1                                     resource  0.00
21                                     boardId  0.00
16                                   updatedOn  0.00
13                                  photoCount  0.00
12                                      images  0.00
22                                address.area  0.00
18                                   openHouse  0.00
23                                address.city  0.00
3                                        class  0.00
26                   address.majorIntersection  0.00
4                                         type  0.00
5                                    listPrice  0.00
29                          address.streetName  0.00
6                                     listDate  0.00
10                               originalPrice  0.00
30                        address.streetNumber  0.00
7                                   lastStatus  0.00
19                                       rooms  0.00
31                        address.streetSuffix  0.01
15                                   occupancy  0.04
61                     details.numGarageSpaces  0.09
123                                  lot.depth  0.11
126                            lot.measurement  0.11
27                        address.neighborhood  0.11
127                                  lot.width  0.12
137                         taxes.annualAmount  0.22
125                       lot.legalDescription  0.22
138                       taxes.assessmentYear  0.22
52                              details.extras  0.27
25                            address.district  0.30
60                       details.numFireplaces  0.32
62                    details.numParkingSpaces  0.41
14                                daysOnMarket  0.41
47                                 details.den  0.41
8                                    soldPrice  0.41
100                           details.driveway  0.42
64                        details.numRoomsPlus  0.48
35                       address.communityCode  0.48
71                           details.yearBuilt  0.48
67           

In [6]:
na_percentage = df.isna().mean().reset_index()
df = df[[x for x in df.columns if x not in list(na_percentage[na_percentage[0] >= 0.5]['index'])]]

In [7]:
df.columns.to_list()

['mlsNumber',
 'resource',
 'status',
 'class',
 'type',
 'listPrice',
 'listDate',
 'lastStatus',
 'soldPrice',
 'originalPrice',
 'images',
 'photoCount',
 'daysOnMarket',
 'occupancy',
 'updatedOn',
 'coopCompensation',
 'openHouse',
 'rooms',
 'agents',
 'boardId',
 'address.area',
 'address.city',
 'address.district',
 'address.majorIntersection',
 'address.neighborhood',
 'address.streetName',
 'address.streetNumber',
 'address.streetSuffix',
 'address.zip',
 'address.state',
 'address.communityCode',
 'map.latitude',
 'map.longitude',
 'map.point',
 'permissions.displayAddressOnInternet',
 'permissions.displayPublic',
 'permissions.displayInternetEntireListing',
 'details.airConditioning',
 'details.basement1',
 'details.den',
 'details.description',
 'details.exteriorConstruction1',
 'details.extras',
 'details.garage',
 'details.heating',
 'details.numBathrooms',
 'details.numBedrooms',
 'details.numFireplaces',
 'details.numGarageSpaces',
 'details.numParkingSpaces',
 'detail

In [8]:
for i in df.columns.to_list():
    print(df[i].describe())

count           100
unique           84
top       X10421506
freq              2
Name: mlsNumber, dtype: object
count               100
unique                2
top       Property:2381
freq                 59
Name: resource, dtype: object
count     100
unique      1
top         A
freq      100
Name: status, dtype: object
count                     100
unique                      1
top       ResidentialProperty
freq                      100
Name: class, dtype: object
count      100
unique       2
top       Sale
freq        78
Name: type, dtype: object
count    1.000000e+02
mean     1.044883e+06
std      9.264320e+05
min      1.750000e+03
25%      3.750000e+05
50%      8.919440e+05
75%      1.382425e+06
max      4.299000e+06
Name: listPrice, dtype: float64
count                               100
unique                                1
top       2024-11-13T00:00:00.000-00:00
freq                                100
Name: listDate, dtype: object
count     100
unique      1
top       New
freq  

In [9]:
feature_list = ['mlsNumber',
 'listPrice',
 'lastStatus',
 'soldPrice',
 'daysOnMarket',
 'address.district',
 'map.latitude',
 'map.longitude',
 'details.airConditioning',
 'details.basement1',
 'details.den',
 'details.exteriorConstruction1',
 'details.garage',
 'details.numBathrooms',
 'details.numBedrooms',
 'details.numFireplaces',
 'details.numGarageSpaces',
 'details.numParkingSpaces',
 'details.numRooms',
 'details.numRoomsPlus',
 'details.propertyType',
 'details.sqft',
 'details.style',
 'details.yearBuilt',
 'details.familyRoom',
 'details.numKitchens',
 'lot.depth',
 'lot.width',
 'nearby.amenities',
 'taxes.annualAmount']

In [10]:
df = df[feature_list]


In [11]:
df.head()

mlsNumber  listPrice lastStatus  soldPrice  daysOnMarket address.district  \
0  X10421506     688000        New        NaN           NaN             None   
1  N10421482    1738000        New        0.0           0.0    Richmond Hill   
2  W10421557     825000        New        0.0           0.0      Toronto W04   
3  X10421506     688000        New        0.0           0.0    Niagara Falls   
4  W10421494     799900        New        0.0           0.0      Toronto W03   

   map.latitude  map.longitude details.airConditioning  \
0     43.105279     -79.069911             Central Air   
1     43.901048     -79.461480             Central Air   
2     43.706359     -79.529639             Central Air   
3     43.105290     -79.070014             Central Air   
4     43.679507     -79.499163             Central Air   

             details.basement1 details.den details.exteriorConstruction1  \
0  Finished, Separate Entrance        None           Vinyl Siding, Brick   
1                         Full           Y                         Brick   
2                     Finished           N                   Brick Front   
3                     Finished           Y                         Brick   
4                     Finished           N                   Alum Siding   

  details.garage  details.numBathrooms  details.numBedrooms  \
0           None                     5                    6   
1       Attached                     3                    4   
2           None                     2                    2   
3           None                     5                    6   
4       Detached                     2                    3   

  details.numFireplaces  details.numGarageSpaces  details.numParkingSpaces  \
0                     1                      NaN                       NaN   
1                     Y                      2.0                       5.0   
2                     N                      0.0                       0.0   
3                     Y                      0.0                       6.0   
4                     N                      1.0                       3.0   

   details.numRooms  details.numRoomsPlus details.propertyType details.sqft  \
0                10                   2.0             Detached    1500-2000   
1                 8                   1.0             Detached    2500-3000   
2                 6                   2.0             Detached         None   
3                10                   2.0             Detached    1500-2000   
4                 8                   4.0             Detached    1100-1500   

  details.style details.yearBuilt details.familyRoom  details.numKitchens  \
0      2-Storey              100+                  Y                    3   
1      2-Storey              None                  Y                    1   
2      2-Storey              None                  N                    1   
3      2-Storey              100+                  Y                    3   
4      2-Storey              None                  N                    1   

  lot.depth lot.width                                   nearby.amenities  \
0       100     32.61                                                 []   
1    113.32     36.09                                                 []   
2    100.00     20.00            [Library, Park, Public Transit, School]   
3    100.00     32.61                                                 []   
4    125.00     25.00  [Golf, Library, Public Transit, Rec Centre, Sc...   

   taxes.annualAmount  
0             2500.34  
1             7210.00  
2             2703.80  
3             2500.34  
4             3998.47

In [13]:
# model = PCA()
# pca_features = model.fit_transform(df_numerics)
# first_pc = model.components_[0,:]



In [14]:
df.head()

mlsNumber  listPrice lastStatus  soldPrice  daysOnMarket address.district  \
0  X10421506     688000        New        NaN           NaN             None   
1  N10421482    1738000        New        0.0           0.0    Richmond Hill   
2  W10421557     825000        New        0.0           0.0      Toronto W04   
3  X10421506     688000        New        0.0           0.0    Niagara Falls   
4  W10421494     799900        New        0.0           0.0      Toronto W03   

   map.latitude  map.longitude details.airConditioning  \
0     43.105279     -79.069911             Central Air   
1     43.901048     -79.461480             Central Air   
2     43.706359     -79.529639             Central Air   
3     43.105290     -79.070014             Central Air   
4     43.679507     -79.499163             Central Air   

             details.basement1 details.den details.exteriorConstruction1  \
0  Finished, Separate Entrance        None           Vinyl Siding, Brick   
1                         Full           Y                         Brick   
2                     Finished           N                   Brick Front   
3                     Finished           Y                         Brick   
4                     Finished           N                   Alum Siding   

  details.garage  details.numBathrooms  details.numBedrooms  \
0           None                     5                    6   
1       Attached                     3                    4   
2           None                     2                    2   
3           None                     5                    6   
4       Detached                     2                    3   

  details.numFireplaces  details.numGarageSpaces  details.numParkingSpaces  \
0                     1                      NaN                       NaN   
1                     Y                      2.0                       5.0   
2                     N                      0.0                       0.0   
3                     Y                      0.0                       6.0   
4                     N                      1.0                       3.0   

   details.numRooms  details.numRoomsPlus details.propertyType details.sqft  \
0                10                   2.0             Detached    1500-2000   
1                 8                   1.0             Detached    2500-3000   
2                 6                   2.0             Detached         None   
3                10                   2.0             Detached    1500-2000   
4                 8                   4.0             Detached    1100-1500   

  details.style details.yearBuilt details.familyRoom  details.numKitchens  \
0      2-Storey              100+                  Y                    3   
1      2-Storey              None                  Y                    1   
2      2-Storey              None                  N                    1   
3      2-Storey              100+                  Y                    3   
4      2-Storey              None                  N                    1   

  lot.depth lot.width                                   nearby.amenities  \
0       100     32.61                                                 []   
1    113.32     36.09                                                 []   
2    100.00     20.00            [Library, Park, Public Transit, School]   
3    100.00     32.61                                                 []   
4    125.00     25.00  [Golf, Library, Public Transit, Rec Centre, Sc...   

   taxes.annualAmount  
0             2500.34  
1             7210.00  
2             2703.80  
3             2500.34  
4             3998.47

## ETL and Modelling Stage
#### Above code removes missing or overly detailed features
#### Things to do
#### 1) Transform nearby.amenities into one hots (done)
#### 2) Extract address.district, details.airConditioning	details.basement1	details.den	details.exteriorConstruction1	details.extras	###details.garage
#### details.propertyType	details.style	details.swimmingPool	details.yearBuilt	details.familyRoom	details.driveway
#### 3) Lat long scaling
#### 4) Map details.sqft to numerics (done)
#### 5) 'lot.depth' * 'lot.width' feature (done)
#### 6) Look at time metrics 
#### 6) StandardScaler on all numerics
#### 7) Keep one hots and test out


In [15]:
one_hot_cols = ['lastStatus','address.district','details.airConditioning','details.basement1','details.den','details.exteriorConstruction1','details.garage','details.propertyType','details.style','details.familyRoom']
numeric_cols = [ 'soldPrice','listPrice','daysOnMarket','details.numBathrooms','details.numBedrooms','details.numFireplaces','details.numGarageSpaces','details.numParkingSpaces','details.numRooms','details.numRoomsPlus','details.numKitchens','taxes.annualAmount','lot_size','details.sqft','details.yearBuilt']	

In [16]:
for cols in one_hot_cols:
    print(cols)
    print(df[cols].nunique())

lastStatus
1
address.district
43
details.airConditioning
4
details.basement1
22
details.den
2
details.exteriorConstruction1
23
details.garage
6
details.propertyType
1
details.style
10
details.familyRoom
2


In [17]:
unique_amens = set([item for sublist in df['nearby.amenities'] for item in sublist])
unique_amens

{'Beach',
 'Clear View',
 'Cul De Sac',
 'Cul de Sac/Dead End',
 'Electric Car Charger',
 'Fenced Yard',
 'Golf',
 'Greenbelt/Conservation',
 'Hospital',
 'Lake Access',
 'Lake/Pond',
 'Level',
 'Library',
 'Marina',
 'Park',
 'Place Of Worship',
 'Public Transit',
 'Ravine',
 'Rec Centre',
 'Rec./Commun.Centre',
 'River/Stream',
 'School',
 'School Bus Route',
 'Skiing',
 'Waterfront',
 'Wooded/Treed'}

In [18]:
amenity_cols = [ 'School','Greenbelt/Conservation', 'Public Transit', 'Park', 'Public Transit','Rec Centre', 'Waterfront',]
df['school'] = [1 if 'School' in x else 0 for x in df['nearby.amenities']]
df['greenbelt'] = [1 if '/Conserv' in x else 0 for x in df['nearby.amenities']]
df['park'] = [1 if 'Park' in x else 0 for x in df['nearby.amenities']]
df['transit'] = [1 if 'Transit' in x else 0 for x in df['nearby.amenities']]
df['rec_center'] = [1 if 'Centre' in x else 0 for x in df['nearby.amenities']]
df['waterfront'] = [1 if 'Waterfront' in x else 0 for x in df['nearby.amenities']]
df.drop(columns = 'nearby.amenities',inplace=True)

In [19]:
df['details.sqft'].value_counts()

details.sqft
1500-2000    12
2000-2500    12
1100-1500    11
2500-3000     5
3000-3500     4
700-1100      4
3500-5000     3
5000 +        1
Name: count, dtype: int64

In [20]:
df['details.yearBuilt'].value_counts()

details.yearBuilt
51-99    12
0-5      10
6-15      9
100+      8
31-50     8
16-30     4
New       1
Name: count, dtype: int64

In [21]:
df['details.sqft'].replace({'1500-2000':1750,
'2000-2500':2250,
'1100-1500':1300,
'700-1100' :850,
'500-700':600,
'< 500':250,
'3500-5000':4250,
'2500-3000':2750,
'3000-3500':3250,
'3500-4000':3750,
'4000-5000':4500,
'5000 +':5000},inplace=True)

df['details.yearBuilt'].replace({'0-5':2.5,
'51-99':75,
'6-15':11,
'31-50':40,
'100+':100,
'16-30':22,
'New':0},inplace=True)
df['details.numFireplaces'].replace({'Y':1,'N':0},inplace=True)


df['lot.depth'] = df['lot.depth'].astype(float)
df['lot.width'] = df['lot.width'].astype(float)
df['lot_size'] = df['lot.depth']* df['lot.width']
df.drop(columns = ['lot.depth','lot.width'],inplace=True)

/tmp/ipykernel_13181/2680942235.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df['details.sqft'].replace({'1500-2000':1750,
/tmp/ipykernel_13181/2680942235.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df['details.sqft'].replace({'1500-2000':1750,
/tmp/ipykernel_13181/2680942235.py:14: F

In [22]:
[x for x in df.columns if x not in numeric_cols and x not in one_hot_cols]

['mlsNumber',
 'map.latitude',
 'map.longitude',
 'school',
 'greenbelt',
 'park',
 'transit',
 'rec_center',
 'waterfront']

In [44]:
scaler_pipeline = Pipeline([
    ('imputer', SimpleImputer(strategy="median")),
    ('std_scaler', StandardScaler())
])

one_hot_pipeline = Pipeline([
    ('imputer', SimpleImputer(strategy="most_frequent")),
    ('one_hot', OneHotEncoder(sparse_output=False))
])

pipeline = ColumnTransformer([
    ('scalar', scaler_pipeline, numeric_cols),
    ('one_hot', one_hot_pipeline, one_hot_cols)
], remainder='passthrough')

pipeline.fit(df[[x for x in df.columns if x!= 'mlsNumber']])

# Transform the data (this will apply one-hot encoding and leave the numeric columns unchanged)
transformed_data = pipeline.transform(df[[x for x in df.columns if x!= 'mlsNumber']])

In [45]:
transformed_data[0]

array([  0.        ,  -0.3871643 ,   0.        ,   1.29267118,
         2.81464583,   0.51291512,   0.38943391,  -0.19218434,
         0.81875522,  -1.32022608,   5.45668211,  -0.84223191,
        -0.15464707,  -0.27685832,   2.2459695 ,   1.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   0.        ,
         0.        ,   0.        ,   0.        ,   1.        ,
         1.        ,   0.        ,   0.        ,   0.  

In [51]:
df.head(10)

mlsNumber  listPrice lastStatus  soldPrice  daysOnMarket address.district  \
0  X10421506     688000        New        NaN           NaN             None   
1  N10421482    1738000        New        0.0           0.0    Richmond Hill   
2  W10421557     825000        New        0.0           0.0      Toronto W04   
3  X10421506     688000        New        0.0           0.0    Niagara Falls   
4  W10421494     799900        New        0.0           0.0      Toronto W03   
5  X10421567     869990        New        NaN           NaN             None   
6  W10421720     999999        New        NaN           NaN      Orangeville   
7  W10421807    2688000        New        NaN           NaN      Toronto W04   
8  X10421990     799900        New        0.0           0.0          Welland   
9  X10421773       2700        New        0.0           0.0        Brantford   

   map.latitude  map.longitude details.airConditioning  \
0     43.105279     -79.069911             Central Air   
1     43.901048     -79.461480             Central Air   
2     43.706359     -79.529639             Central Air   
3     43.105290     -79.070014             Central Air   
4     43.679507     -79.499163             Central Air   
5     43.077890     -79.931238             Central Air   
6     43.900274     -80.126873             Central Air   
7     43.722066     -79.455277             Central Air   
8     43.019035     -79.254671             Central Air   
9     43.111030     -80.303570             Central Air   

             details.basement1 details.den details.exteriorConstruction1  \
0  Finished, Separate Entrance        None           Vinyl Siding, Brick   
1                         Full           Y                         Brick   
2                     Finished           N                   Brick Front   
3                     Finished           Y                         Brick   
4                     Finished           N                   Alum Siding   
5             Full, Unfinished        None     Brick Front, Vinyl Siding   
6                     Finished        None           Brick, Vinyl Siding   
7            Finished, Walk-Up        None       Stone, Stucco (Plaster)   
8                         Full           N                         Brick   
9                         Full           N                         Brick   

  details.garage  details.numBathrooms  details.numBedrooms  \
0           None                     5                    6   
1       Attached                     3                    4   
2           None                     2                    2   
3           None                     5                    6   
4       Detached                     2                    3   
5       Built-In                     3                    4   
6       Attached                     3                    3   
7       Built-In                     5                    4   
8       Attached                     2                    3   
9       Built-In                     3                    3   

  details.numFireplaces  details.numGarageSpaces  details.numParkingSpaces  \
0                     1                      NaN                       NaN   
1                     1                      2.0                       5.0   
2                     0                      0.0                       0.0   
3                     1                      0.0                       6.0   
4                     0                      1.0                       3.0   
5                  None                      1.5                       NaN   
6                  None                      2.0                       NaN   
7                  None                      2.0                       NaN   
8                     1                      1.5                       4.0   
9                     0                      1.0                       2.0   

   details.numRooms  details.numRoomsPlus details.propertyType  details.sqft  \
0            

## Cosine Similarity Model
####here just looking at reducing dimensions and then generating lists
#

In [69]:
def get_listings(listing_id, cosine_sim, df, n_listing = 10):
    idx = df[df['mlsNumber'] == listing_id].index[0]
    
    sim = list(enumerate(cosine_sim[idx]))
    sim = sorted(sim, key=lambda x: x[1], reverse=True)
    
    sim_output = sim[1:n_listing-1]
    similar_indices = [i[0] for i in sim_output]
    
    return df['mlsNumber'].iloc[similar_indices], df.iloc[similar_indices]

In [70]:
similarities = cosine_similarity(transformed_data, transformed_data)


In [77]:

recommended_ids, recommended_listings = get_listings('W10421807', similarities, df, 20)
print("Recommended listings for :")
print(recommended_ids)

Recommended listings for :
13    N10422086
78    W10421725
38    N10421524
57    C10421593
87    W10421826
65    W10421764
43    X10421633
84    N10421740
39    X10422355
1     N10421482
15    X10421966
73    X10421836
89    W10422194
76    N10421891
59    N10421532
91    C10422413
64    W10421764
83    W10421723
Name: mlsNumber, dtype: object


In [78]:
df[df.mlsNumber == 'W10421807']

mlsNumber  listPrice lastStatus  soldPrice  daysOnMarket address.district  \
7  W10421807    2688000        New        NaN           NaN      Toronto W04   

   map.latitude  map.longitude details.airConditioning  details.basement1  \
7     43.722066     -79.455277             Central Air  Finished, Walk-Up   

  details.den details.exteriorConstruction1 details.garage  \
7        None       Stone, Stucco (Plaster)       Built-In   

   details.numBathrooms  details.numBedrooms details.numFireplaces  \
7                     5                    4                  None   

   details.numGarageSpaces  details.numParkingSpaces  details.numRooms  \
7                      2.0                       NaN                11   

   details.numRoomsPlus details.propertyType  details.sqft details.style  \
7                   NaN             Detached        4250.0      2-Storey   

   details.yearBuilt details.familyRoom  details.numKitchens  \
7                2.5                  Y                    1   

   taxes.annualAmount  school  greenbelt  park  transit  rec_center  \
7             10050.0       0          0     0        0           0   

   waterfront  lot_size  
7           0    5200.0

In [79]:

recommended_listings

mlsNumber  listPrice lastStatus  soldPrice  daysOnMarket  \
13  N10422086    2199999        New        0.0           0.0   
78  W10421725    1398000        New        NaN           NaN   
38  N10421524    2888000        New        0.0           0.0   
57  C10421593    3388000        New        NaN           NaN   
87  W10421826    1950000        New        0.0           0.0   
65  W10421764    1149000        New        NaN           NaN   
43  X10421633    1079000        New        NaN           NaN   
84  N10421740    1390000        New        0.0           0.0   
39  X10422355    3299900        New        NaN           NaN   
1   N10421482    1738000        New        0.0           0.0   
15  X10421966    2499000        New        NaN           NaN   
73  X10421836     924900        New        0.0           0.0   
89  W10422194    2688000        New        0.0           0.0   
76  N10421891     948000        New        NaN           NaN   
59  N10421532     888888        New        NaN           NaN   
91  C10422413    3189000        New        0.0           0.0   
64  W10421764    1149000        New        0.0           0.0   
83  W10421723    2549900        New        NaN           NaN   

             address.district  map.latitude  map.longitude  \
13                       King     43.903174     -79.661909   
78                       None     43.711405     -79.470638   
38                    Markham     43.886092     -79.318500   
57                Toronto C14     43.782536     -79.392375   
87                    Caledon     43.874258     -79.869977   
65                       None     43.712789     -79.840579   
43                       None     43.396720     -80.382098   
84                   Innisfil     44.293370     -79.552245   
39                   Hamilton     43.237631     -79.959969   
1               Richmond Hill     43.901048     -79.461480   
15  Smith-Ennismore-Lakefield     44.430911     -78.360086   
73             Kawartha Lakes     44.369905     -78.751047   
89                   Oakville     43.409529     -79.719856   
76                       None     44.161761     -79.867840   
59                       None     44.160532     -79.788466   
91                Toronto C04     43.704832     -79.416108   
64                   Brampton     43.712803     -79.840610   
83                       None     43.654232     -79.792620   

   details.airConditioning              details.basement1 details.den  \
13             Central Air                           Full           Y   
78             Central Air  Separate Entrance, Unfinished        None   
38             Central Air                      Apartment           Y   
57             Central Air             Finished, Walk-Out        None   
87             Central Air                           Full           Y   
65             Central Air                       Finished        None   
43             Central Air                     Unfinished        None   
84             Central Air                       Part Fin           N   
39             Central Air               Full, Unfinished        None   
1              Central Air                           Full           Y   
15             Central Air   Finished with Walk-Out, Full        None   
73             Central Air                       Finished           Y   
89             Central Air                       Finished           Y   
76             Central Air                       Finished        None   
59             Central Air                     Unfinished        None   
91             Central Air                        Fin W/O           Y   
64             Central Air                       Finished           N   
83             Central Air         Finished with Walk-Out        None   

   details.exteriorConstruction1 details.garage  details.numBathrooms  \
13                         Stone       Attached                     5   
78                         Brick       Attached                     4   
3

In [76]:
df.head(30)

mlsNumber  listPrice lastStatus  soldPrice  daysOnMarket  \
0   X10421506     688000        New        NaN           NaN   
1   N10421482    1738000        New        0.0           0.0   
2   W10421557     825000        New        0.0           0.0   
3   X10421506     688000        New        0.0           0.0   
4   W10421494     799900        New        0.0           0.0   
5   X10421567     869990        New        NaN           NaN   
6   W10421720     999999        New        NaN           NaN   
7   W10421807    2688000        New        NaN           NaN   
8   X10421990     799900        New        0.0           0.0   
9   X10421773       2700        New        0.0           0.0   
10  W10421720     999999        New        0.0           0.0   
11  X10421837       3000        New        0.0           0.0   
12  X10421837       3000        New        NaN           NaN   
13  N10422086    2199999        New        0.0           0.0   
14  E10422078    1799000        New        NaN           NaN   
15  X10421966    2499000        New        NaN           NaN   
16  X10422113     899900        New        0.0           0.0   
17  W10421973       4600        New        0.0           0.0   
18  C10421915    1598000        New        0.0           0.0   
19  W10421998       2050        New        0.0           0.0   
20  W10421527       2299        New        NaN           NaN   
21  W10421527       2299        New        0.0           0.0   
22  S10421548     675000        New        NaN           NaN   
23  W10421542    2249888        New        NaN           NaN   
24  X10421484     759900        New        0.0           0.0   
25  W10421674       3499        New        NaN           NaN   
26  X10421647       2595        New        0.0           0.0   
27  X10421647       2595        New        NaN           NaN   
28  W10421712       3700        New        0.0           0.0   
29  E10421743       3450        New        0.0           0.0   

             address.district  map.latitude  map.longitude  \
0                        None     43.105279     -79.069911   
1               Richmond Hill     43.901048     -79.461480   
2                 Toronto W04     43.706359     -79.529639   
3               Niagara Falls     43.105290     -79.070014   
4                 Toronto W03     43.679507     -79.499163   
5                        None     43.077890     -79.931238   
6                 Orangeville     43.900274     -80.126873   
7                 Toronto W04     43.722066     -79.455277   
8                     Welland     43.019035     -79.254671   
9                   Brantford     43.111030     -80.303570   
10                Orangeville     43.900270     -80.126855   
11                  Kitchener     43.408950     -80.501275   
12                       None     43.408917     -80.501218   
13                       King     43.903174     -79.661909   
14                       None     43.669496     -79.310069   
15  Smith-Ennismore-Lakefield     44.430911     -78.360086   
16                  Kitchener     43.381627     -80.441714   
17                   Oakville     43.507348     -79.706378   
18                Toronto C14     43.780331     -79.398840   
19                     Milton     43.490982     -79.866908   
20                   Brampton     43.667850     -79.757417   
21                   Brampton     43.667836     -79.757419   
22                       None     44.419481     -80.101840   
23                       None     43.672879     -79.566153   
24                  Haldimand     43.065701     -79.967638   
25                   Brampton     43.686100     -79.853196   
26                     Guelph     43.538501     -80.272773   
27                       None     43.538497     -80.272762   
28                   Brampton     43.759705     -79.780039   
29                     Whitby     43.933615     -78.964509   

   details.airConditioning             details.basement1 details.den  \
0              Central A